Итоговая работа
=====================

Представлены данные такси, по которым мы должны предсказать возьмёт ли таксист заказ или нет(driver_response).

Чек-лист:
1. Загрузите датасет taxi.csv.
2. Посмотрите на данные. Отобразите общую информацию по признакам (вспомните о describe и info). Напишите в markdown свои наблюдения.
3. Выявите пропуски, а также возможные причины их возникновения. Решите, что следует сделать с ними. Напишите в markdown свои наблюдения.
4. Оцените зависимости переменных между собой. Используйте корреляции. Будет хорошо, если воспользуетесь profile_report. Напишите в markdown свои наблюдения.
5. Определите стратегию преобразования категориальных признаков (т.е. как их сделать адекватными для моделей).
6. Найдите признаки, которые можно разделить на другие, или преобразовать в другой тип данных. Удалите лишние, при необходимости.
7. Разделите выборку на обучаемую и тестовую.
8. Обучите модель. Напишите в markdown свои наблюдения по полученным результатам. Хорошие результаты дают классификаторы RandomForest и XGBoost


In [3]:
import pandas as pd
import numpy as np
import seaborn as sns
from matplotlib import pyplot as plt

In [5]:
data = pd.read_csv('taxi.csv')
data.head(5)

offer_gk  weekday_key  hour_key  driver_gk  order_gk  driver_latitude  \
0   1105373            5        20       6080    174182        55.818842   
1    759733            5        14       6080    358774        55.805342   
2    416977            6        14       6080    866260        55.813978   
3    889660            2         6       6080    163522        55.745922   
4   1120055            4        16       6080    506710        55.803578   

   driver_longitude  origin_order_latitude  origin_order_longitude  \
0         37.334562              55.814567               37.355010   
1         37.515023              55.819329               37.466398   
2         37.347688              55.814827               37.354074   
3         37.421748              55.743469               37.431130   
4         37.521602              55.812559               37.527407   

   distance_km  duration_min offer_class_group ride_type_desc  driver_response  
0       -1.000        -1.000           Economy        private                0  
1       18.802        25.217          Standard        private                1  
2        6.747         9.800           Economy        private                0  
3       -1.000        -1.000           Economy        private                1  
4       12.383        19.250           Economy        private                1

In [4]:
pip install pandas_profiling

Note: you may need to restart the kernel to use updated packages.


In [9]:
import pandas_profiling

In [10]:
data.profile_report()

В датасете 14 признаков, 100 тысяч строк (заказов такси). Пропущенных значений, дублирующих строк нет. 
Наблюдаются признаки с сильной корреляцией между собой:

Рассмотрим все признаки:

'offer_gk' - номер предложения. Индивидуален для каждой строки датасета. Не несет для модели никакой смысловой нагрузки. Не будем использовать при обучении модели (удалим).

'weekday_key' - указывает на день недели заказа. Категориальный числовой признак, принимает дискретно целые значения от 0 до 6 (7 дней недели).

'hour_key' - указывает на час заказа. Категориальный числовой признак. Принимает дискретно целые значения от 0 до 23 (24 часа).

'driver_gk' - номер водителя. Всего в датасете рассматриваются 429 водителей (на датасет из 100 тыс. заказов).

'order_gk' - номер заказа. Уникальных значений меньше, чем выборка. Нужен дополнительный анализ признака.

'driver_latitude', 'driver_longitude' - координаты водителя во время заказа. Наблюдается высокая корреляция между признаками (ρ = 0.9861978482), но пока оставим оба признака в выборке для построения модели. Имеются значения -1 (140 значений) и 0 (1 значение), что можно считать вылетом. Нужна дополнительная обработка.

'origin_order_latitude', 'origin_order_longitude' - координаты точки заказа. Имеются значения -1 (13 значений), что можно считать вылетом. Нужна дополнительная обработка.

'distance_km' - количество километров в заказе. Порядка 26% значений = -1. предполагаю, что в таких заказах пользователем не указывается точка завершения заказа (поездка по счетчику). Кроме того наблюдается перекос данных  - есть ряд значений с большим расстоянием. Необходим дополнительный анализ.

'duration_min' - количество минут на выполнение заказа. Также (мое предположение) принмает значение -1 в случае отсутствия указанной в заказе точки завершения заказа. Имеет сильную корреляцию с 'distance_km' (ρ = 0.977033326), что логино - время поездки сильно зависит от расстояния поездки. В силу большой корреляции между признаками откажемся от одного из них ('duration_min') при обучении модели.

'offer_class_group' - класс заказа. Принимает 9 значений - категориальный признак. Обработать.

'ride_type_desc' - тип заказа (SMB, affiliate, buissness, peivate). Категориальный признак, принимает 4 значения. Обработать.

'driver_response' - таргет. Ответ водителя, готов он взять заказ или нет.

Итого:
    
Удалить: 'offer_gk', 'duration_min'
    
Дополнительно посмотреть: 'order_gk' , 'distance_km', 'driver_latitude', 'driver_longitude', 'origin_order_latitude', 'origin_order_longitude'    

Обработать категориальные признаки: 'offer_class_group', 'ride_type_desc'

1. Анализ признака 'order_gk' 

Посмотрим значения, которые встречаются в датасете чаще всего (согласно статистике профайла)

In [24]:
data[data['order_gk']== 853342]

offer_gk  weekday_key  hour_key  driver_gk  order_gk  driver_latitude  \
23218    929594            5        23       4339    853342        55.966694   
23484    574355            5        23        801    853342        55.961051   
23651    394516            5        23       2236    853342        55.962323   
24326    609443            5        23       4600    853342        55.962324   
24651    726807            5        23       4804    853342        55.960693   
24926   1066357            5        23       4100    853342        55.961092   
25672    338185            5        23       1793    853342        55.962122   
26857    882098            5        23        668    853342        55.962427   
27009    937263            5        23       2381    853342        55.961857   
27502     16487            5        23       1060    853342        55.961859   
30282    345109            5        23       5917    853342        55.961061   
31008    149010            5        23       6290    853342        55.965095   
31179    127613            5        23       6762    853342        55.964892   
32631    591326            5        23       4735    853342        55.965487   

       driver_longitude  origin_order_latitude  origin_order_longitude  \
23218         37.415752              55.962322               37.407117   
23484         37.415866              55.962322               37.407117   
23651         37.407117              55.962322               37.407117   
24326         37.407116              55.962322               37.407117   
24651         37.415349              55.962322               37.407117   
24926         37.413188              55.962322               37.407117   
25672         37.409464              55.962322               37.407117   
26857         37.409279              55.962322               37.407117   
27009         37.414049              55.962322               37.407117   
27502         37.407126              55.962322               37.407117   
30282         37.413291              55.962322               37.407117   
31008         37.429087              55.962322               37.407117   
31179         37.413543              55.962322               37.407117   
32631         37.431341              55.962322               37.407117   

       distance_km  duration_min offer_class_group ride_type_desc  \
23218        7.718          16.7           Economy        private   
23484        7.718          16.7           Economy        private   
23651        7.718          16.7           Economy        private   
24326        7.718          16.7           Economy        private   
24651        7.718          16.7           Economy        private   
24926        7.718          16.7           Economy        private   
25672        7.718          16.7           Economy        private   
26857        7.718          16.7           Economy        private   
27009        7.718          16.7           Economy        private   
27502        7.718          16.7           Economy        private   
30282        7.718          16.7           Economy        private   
31008        7.718          16.7           Economy        private   
31179        7.718          16.7           Economy        private   
32631        7.718          16.7           Economy        private   

       driver_response  
23218                0  
23484                0  
23651                0  
24326                0  
24651                0  
24926                0  
25672                0  
26857                0  
27009                0  
27502                0  
30282                0  
31008                0  
31179                0  
32631                0

In [25]:
data[data['order_gk']== 714527]

offer_gk  weekday_key  hour_key  driver_gk  order_gk  driver_latitude  \
23937    843964            1        23       2236    714527        55.962323   
25230    356596            1        23       4100    714527        55.961150   
26156    374670            1        23       1793    714527        55.962122   
27246    728761            1        23       2381    714527        55.961529   
28614   1013331            1        23       1060    714527        55.961859   
30582   1011258            1        23       5917    714527        55.962323   
39611    837367            1        23       1421    714527        55.961175   
73393     93487            1        23        462    714527        55.962068   
77993    508640            1        23       2063    714527        55.962325   
88687     10636            1        23       1358    714527        55.964893   
91564    261173            1        23       2816    714527        55.964304   
95645    817410            1        23       1126    714527        55.962987   
99125    108889            1        23       2442    714527        55.961376   

       driver_longitude  origin_order_latitude  origin_order_longitude  \
23937         37.407117              55.966694               37.415754   
25230         37.413188              55.966694               37.415754   
26156         37.409464              55.966694               37.415754   
27246         37.413888              55.966694               37.415754   
28614         37.407126              55.966694               37.415754   
30582         37.407117              55.966694               37.415754   
39611         37.413284              55.966694               37.415754   
73393         37.417515              55.966694               37.415754   
77993         37.407117              55.966694               37.415754   
88687         37.413543              55.966694               37.415754   
91564         37.423557              55.966694               37.415754   
95645         37.413468              55.966694               37.415754   
99125         37.413864              55.966694               37.415754   

       distance_km  duration_min offer_class_group ride_type_desc  \
23937       42.946        43.617           Economy        private   
25230       42.946        43.617           Economy        private   
26156       42.946        43.617           Economy        private   
27246       42.946        43.617           Economy        private   
28614       42.946        43.617           Economy        private   
30582       42.946        43.617           Economy        private   
39611       42.946        43.617           Economy        private   
73393       42.946        43.617           Economy        private   
77993       42.946        43.617           Economy        private   
88687       42.946        43.617           Economy        private   
91564       42.946        43.617           Economy        private   
95645       42.946        43.617           Economy        private   
99125       42.946        43.617           Economy        private   

       driver_response  
23937                0  
25230                0  
26156                0  
27246                0  
28614                0  
30582                0  
39611                0  
73393                0  
77993                1  
88687                0  
91564                0  
95645                0  
99125                0

Видно, что 'order_gk' это по сути номер заявки, которая высылается нескольким водителям в поисках оптимального предложения. Уникальных значений 81435 из 100 000. Мое мнение, что от номера заявки не зависит ответ водителя, поэтому не используем данный признак при обучении модели.

2. Анализ признаков 'driver_latitude', 'driver_longitude' 

Имеются значения -1 (140 значений) и 0 (1 значение), что можно считать вылетом. Т.к. строк с вылетами очень малое количество по сравнению с рамером выборки, удалим эти строки.

In [35]:
data_1 = data.query('driver_latitude > 0')
data_1 = data.query('driver_longitude > 0')
data_1.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 99859 entries, 0 to 99999
Data columns (total 14 columns):
offer_gk                  99859 non-null int64
weekday_key               99859 non-null int64
hour_key                  99859 non-null int64
driver_gk                 99859 non-null int64
order_gk                  99859 non-null int64
driver_latitude           99859 non-null float64
driver_longitude          99859 non-null float64
origin_order_latitude     99859 non-null float64
origin_order_longitude    99859 non-null float64
distance_km               99859 non-null float64
duration_min              99859 non-null float64
offer_class_group         99859 non-null object
ride_type_desc            99859 non-null object
driver_response           99859 non-null int64
dtypes: float64(6), int64(6), object(2)
memory usage: 11.4+ MB


3. Анализ признаков 'origin_order_latitude', 'origin_order_longitude'
Имеются значения -1 (13 значений), что можно считать вылетом. Т.к. строк с вылетами очень малое количество по сравнению с рамером выборки, удалим эти строки.

In [37]:
data_2 = data_1.query('origin_order_latitude > 0')
data_2 = data_1.query('origin_order_longitude > 0')
data_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 99846 entries, 0 to 99999
Data columns (total 14 columns):
offer_gk                  99846 non-null int64
weekday_key               99846 non-null int64
hour_key                  99846 non-null int64
driver_gk                 99846 non-null int64
order_gk                  99846 non-null int64
driver_latitude           99846 non-null float64
driver_longitude          99846 non-null float64
origin_order_latitude     99846 non-null float64
origin_order_longitude    99846 non-null float64
distance_km               99846 non-null float64
duration_min              99846 non-null float64
offer_class_group         99846 non-null object
ride_type_desc            99846 non-null object
driver_response           99846 non-null int64
dtypes: float64(6), int64(6), object(2)
memory usage: 11.4+ MB


4. Проанализируем 'distance_km'

Согласно профайлу есть 26% значений -1. Мы считаем, что это заказы без определния точки доставки. Данные нас устраивают.

Согласно профайлу максимальные значения признака нереально высокие. Посмотрим, сколько значений превышает отметку 200 км. Все, что выше 200 км считаем вылетом - маловероятно, что это реальный заказ. 

In [130]:
len(data_2.query('distance_km > 200'))

71

Относительно размера датасета количество вылетов по крайне мало. Удалим эти строки.

In [134]:
data_3 = data_2.query('distance_km < 200')
data_3.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 99775 entries, 0 to 99999
Data columns (total 14 columns):
offer_gk                  99775 non-null int64
weekday_key               99775 non-null int64
hour_key                  99775 non-null int64
driver_gk                 99775 non-null int64
order_gk                  99775 non-null int64
driver_latitude           99775 non-null float64
driver_longitude          99775 non-null float64
origin_order_latitude     99775 non-null float64
origin_order_longitude    99775 non-null float64
distance_km               99775 non-null float64
duration_min              99775 non-null float64
offer_class_group         99775 non-null object
ride_type_desc            99775 non-null object
driver_response           99775 non-null int64
dtypes: float64(6), int64(6), object(2)
memory usage: 11.4+ MB


5. Удалим 'offer_gk', 'duration_min', 'order_gk'

In [135]:
data_4 = data_3.drop(['offer_gk', 'duration_min', 'order_gk'], axis=1)

5. Приведем категориальные признаки 'offer_class_group', 'ride_type_desc' к виду векторов с помощью one hot encoding

In [38]:
from sklearn import preprocessing

In [136]:
class_group = data_4['offer_class_group'].get_values().reshape(-1, 1)

In [137]:
class_encoder = preprocessing.OneHotEncoder()
class_encoder.fit(class_group)
class_result = class_encoder.transform(class_group).toarray()
class_result

array([[0., 1., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 1., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 1., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [138]:
type_group = data_4['ride_type_desc'].get_values().reshape(-1, 1)

In [139]:
type_encoder = preprocessing.OneHotEncoder()
type_encoder.fit(type_group)
type_result = type_encoder.transform(type_group).toarray()
type_result

array([[0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       ...,
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.]])

In [140]:
class_columns = ['class_{}'.format(i) for i in range(class_result.shape[1])]
type_columns = ['type_{}'.format(i) for i in range(type_result.shape[1])]

In [141]:
class_df = pd.DataFrame(class_result, columns=class_columns)
class_df.index = data_4.index
type_df = pd.DataFrame(type_result, columns=type_columns)
type_df.index = data_4.index

In [142]:
data_oh1 = pd.concat([data_4, class_df], axis=1)
data_oh1 = data_oh1.drop(['offer_class_group'], axis=1)
data_oh = pd.concat([data_oh1, type_df], axis=1)
data_oh = data_oh.drop([ 'ride_type_desc'], axis=1)
data_oh.head()

weekday_key  hour_key  driver_gk  driver_latitude  driver_longitude  \
0            5        20       6080        55.818842         37.334562   
1            5        14       6080        55.805342         37.515023   
2            6        14       6080        55.813978         37.347688   
3            2         6       6080        55.745922         37.421748   
4            4        16       6080        55.803578         37.521602   

   origin_order_latitude  origin_order_longitude  distance_km  \
0              55.814567               37.355010       -1.000   
1              55.819329               37.466398       18.802   
2              55.814827               37.354074        6.747   
3              55.743469               37.431130       -1.000   
4              55.812559               37.527407       12.383   

   driver_response  class_0  ...  class_3  class_4  class_5  class_6  class_7  \
0                0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
1                1      0.0  ...      0.0      1.0      0.0      0.0      0.0   
2                0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
3                1      0.0  ...      0.0      0.0      0.0      0.0      0.0   
4                1      0.0  ...      0.0      0.0      0.0      0.0      0.0   

   class_8  type_0  type_1  type_2  type_3  
0      0.0     0.0     0.0     0.0     1.0  
1      0.0     0.0     0.0     0.0     1.0  
2      0.0     0.0     0.0     0.0     1.0  
3      0.0     0.0     0.0     0.0     1.0  
4      0.0     0.0     0.0     0.0     1.0  

[5 rows x 22 columns]

In [143]:
data_oh.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 99775 entries, 0 to 99999
Data columns (total 22 columns):
weekday_key               99775 non-null int64
hour_key                  99775 non-null int64
driver_gk                 99775 non-null int64
driver_latitude           99775 non-null float64
driver_longitude          99775 non-null float64
origin_order_latitude     99775 non-null float64
origin_order_longitude    99775 non-null float64
distance_km               99775 non-null float64
driver_response           99775 non-null int64
class_0                   99775 non-null float64
class_1                   99775 non-null float64
class_2                   99775 non-null float64
class_3                   99775 non-null float64
class_4                   99775 non-null float64
class_5                   99775 non-null float64
class_6                   99775 non-null float64
class_7                   99775 non-null float64
class_8                   99775 non-null float64
type_0           

In [117]:
data_oh.profile_report()

Данные первично обработаны. Обучаем модель на полученном датасете data_oh.

Разделим данные на тестовые и тренировочные 20/80

In [61]:
from sklearn.model_selection import train_test_split

In [160]:
X = data_oh.drop(['driver_response'], axis=1)
y = data_oh.driver_response

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=30)

Для обучения модели используем случайный лес

In [96]:
from sklearn.ensemble import RandomForestClassifier

In [161]:
model=RandomForestClassifier(n_estimators=100)

In [162]:
model.fit(X_train,y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [163]:
model.score(X_test, y_test)

0.8107241292909045

Модель обучена с точностью чуть более 80%.

**Посмотрим на дополнительное преобразование данных в датасете.**
Попробуем уменьшить количество признаков - координаты водителя и точки заказа (4 признака) приведем к одному признаку - расстоянию до заказа.

In [164]:
def distance_order(a):
    s = ((a['origin_order_latitude'] - a['driver_latitude'])**2 + (a['origin_order_longitude'] - a['driver_longitude'])**2)**1/2
    return s

In [165]:
data_oh['distance_order'] = data_oh.apply(distance_order, axis=1)
data_oh.head()

weekday_key  hour_key  driver_gk  driver_latitude  driver_longitude  \
0            5        20       6080        55.818842         37.334562   
1            5        14       6080        55.805342         37.515023   
2            6        14       6080        55.813978         37.347688   
3            2         6       6080        55.745922         37.421748   
4            4        16       6080        55.803578         37.521602   

   origin_order_latitude  origin_order_longitude  distance_km  \
0              55.814567               37.355010       -1.000   
1              55.819329               37.466398       18.802   
2              55.814827               37.354074        6.747   
3              55.743469               37.431130       -1.000   
4              55.812559               37.527407       12.383   

   driver_response  class_0  ...  class_4  class_5  class_6  class_7  class_8  \
0                0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
1                1      0.0  ...      1.0      0.0      0.0      0.0      0.0   
2                0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
3                1      0.0  ...      0.0      0.0      0.0      0.0      0.0   
4                1      0.0  ...      0.0      0.0      0.0      0.0      0.0   

   type_0  type_1  type_2  type_3  distance_order  
0     0.0     0.0     0.0     1.0        0.000218  
1     0.0     0.0     0.0     1.0        0.001280  
2     0.0     0.0     0.0     1.0        0.000021  
3     0.0     0.0     0.0     1.0        0.000047  
4     0.0     0.0     0.0     1.0        0.000057  

[5 rows x 23 columns]

In [166]:
data_dist = data_oh.drop(['origin_order_latitude', 'driver_latitude', 'origin_order_longitude', 'driver_longitude'], axis=1)
data_dist.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 99775 entries, 0 to 99999
Data columns (total 19 columns):
weekday_key        99775 non-null int64
hour_key           99775 non-null int64
driver_gk          99775 non-null int64
distance_km        99775 non-null float64
driver_response    99775 non-null int64
class_0            99775 non-null float64
class_1            99775 non-null float64
class_2            99775 non-null float64
class_3            99775 non-null float64
class_4            99775 non-null float64
class_5            99775 non-null float64
class_6            99775 non-null float64
class_7            99775 non-null float64
class_8            99775 non-null float64
type_0             99775 non-null float64
type_1             99775 non-null float64
type_2             99775 non-null float64
type_3             99775 non-null float64
distance_order     99775 non-null float64
dtypes: float64(15), int64(4)
memory usage: 15.2 MB


In [167]:
X_dist = data_dist.drop(['driver_response'], axis=1)
y_dist = data_dist.driver_response

X_train_dist, X_test_dist, y_train_dist, y_test_dist = train_test_split(X_dist, y_dist, test_size=0.2, random_state=30)

In [168]:
model_dist=RandomForestClassifier(n_estimators=100)

In [169]:
model_dist.fit(X_train_dist,y_train_dist)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [170]:
model_dist.score(X_test_dist, y_test_dist)

0.7623653219744425

Видим, что преобразование координат в расстояние не дало лучших результатов. Модель обучилась хуже - точность 76%. 

Возможно, это связано с тем, что расстояние "напрямую" не есть путь от точки положения ТС до точки заказа. Путь, в свою очередь, может быть примерно равным расстоянию "напрямую" или же быть много больше (объезд, например, односторонние улицы и.т.п). Получается, что координаты, лучше описывают расстояние между точками заказа и ТС.

**Вывод: в качестве датасета для обучения модели с помощью RandomForest использовать преобразованный датасет data_oh.**